In [1]:
from astropy.io import fits
from astropy.table import Table, hstack
from astropy.coordinates import SkyCoord, match_coordinates_sky
from astropy import units as u
import numpy as np
import healpy as hp
import matplotlib.pyplot as plt
import math
from multiprocessing import Pool

In [2]:
# constants used by program
max_sep = 0.5 * u.arcsec
debug = True
nSides = 32
dispSides = 4096
channel = 'I'

In [3]:
# file related data
dir_name = '/home/s1/djsuson/data/'
hsc_file_name = 
hsc_file_name = 'hsc_overlap_v2.fits'
delve_file_name = 'delve_overlap.fits'
delve_hsc_file_name = 'delve2hsc_v2.fits'
hsc_delve_file_name = 'hsc2delve_v2.fits'

In [4]:
# read in HSC data
with fits.open(dir_name+hsc_file_name, memmap=True) as hsc_hdu:
    hsc_data = Table(hsc_hdu[1].data)
    
# read in Delve data
with fits.open(dir_name+delve_file_name, memmap=True) as delve_hdu:
    delve_data = Table(delve_hdu[1].data)
    
# find overlapping objects
delve_sky = SkyCoord(ra=delve_data['RA']*u.degree, dec=delve_data['DEC']*u.degree)    
hsc_sky = SkyCoord(ra=hsc_data['ra']*u.degree, dec=hsc_data['dec']*u.degree)

In [5]:
# map delve objects on to hsc
idx, d2d, d3d = match_coordinates_sky(delve_sky, hsc_sky)
sep_constraint = d2d < max_sep
delve_hsc_data = hstack([delve_data[sep_constraint], hsc_data[idx[sep_constraint]]])

# save as a fits file
delve_hsc_data.write(dir_name+delve_hsc_file_name)
with fits.open(dir_name+delve_hsc_file_name, memmap=True, mode='update') as hdu:
    hdr = hdu[0].header
    hdr['comment'] = 'Combined DELVE and HSC catalog of objects with a separation of less than'
    hdr['comment'] = f'{max_sep} arc seconds'
    hdr['comment'] = 'Matches DELVE objects to HSC catalog'
    hdu.flush()

In [6]:
# map hsc objects on to delve
idx, d2d, d3d = match_coordinates_sky(hsc_sky, delve_sky)
sep_constraint = d2d < max_sep
delve_hsc_data = hstack([delve_data[idx[sep_constraint]], hsc_data[sep_constraint]])

# save as a fits file
delve_hsc_data.write(dir_name+hsc_delve_file_name)
with fits.open(dir_name+hsc_delve_file_name, memmap=True, mode='update') as hdu:
    hdr = hdu[0].header
    hdr['comment'] = 'Combined DELVE and HSC catalog of objects with a separation of less than'
    hdr['comment'] = f'{max_sep} arc seconds'
    hdr['comment'] = 'Matches HSC objects to DELVE catalog'
    hdu.flush()